Notebook to retrieve cities names from coordinates using reverse geocoding

In [43]:
import requests
import json

f = open('./networks/outdoor_recreation_network_USA.json')
 
# returns JSON object as
# a dictionary
data = json.load(f)

# elements = data.get("elements")

# nodes = elements.get("nodes")
# edges = elements.get("edges")

# nodes = [{'id': n.get('data').get('id'), 'latitude': n.get('data').get('latitude') , 'longitude': n.get('data').get('longitude'), 'bipartite' : n.get('data').get('bipartite')} for n in nodes]

for i,node in enumerate(nodes): 
    if node.get('bipartite') == 'city':
        lat = float(node.get("latitude"))
        lon = float(node.get("longitude"))
        response = requests.get(
            "https://nominatim.openstreetmap.org/reverse?format=json&lat={}&lon={}".format(lat,lon)
        )
        node_data = response.json()
        city = node_data.get('address').get('city')
        # print(node_data)
        node['city'] = city

ConnectionError: HTTPSConnectionPool(host='nominatim.openstreetmap.org', port=443): Max retries exceeded with url: /reverse?format=json&lat=35.91537&lon=-94.969956 (Caused by NameResolutionError("<urllib3.connection.HTTPSConnection object at 0x7f27580ebda0>: Failed to resolve 'nominatim.openstreetmap.org' ([Errno -3] Temporary failure in name resolution)"))

In [45]:
print(nodes)
for i,node in enumerate(nodes): 
    if node.get('bipartite') == 'city' and node.get('city') == None:
        lat = float(node.get("latitude"))
        lon = float(node.get("longitude"))
        response = requests.get(
            "https://nominatim.openstreetmap.org/reverse?format=json&lat={}&lon={}".format(lat,lon)
        )
        node_data = response.json()
        city = node_data.get('address').get('city')
        # print(node_data)
        node['city'] = city

[{'id': '1', 'latitude': 39.0229714, 'longitude': -94.7145415, 'bipartite': 'city', 'city': 'Shawnee'}, {'id': '2', 'latitude': 38.312105, 'longitude': -95.962768, 'bipartite': 'recarea'}, {'id': '3', 'latitude': 38.92333, 'longitude': -95.33, 'bipartite': 'recarea'}, {'id': '4', 'latitude': 38.654905, 'longitude': -94.900047, 'bipartite': 'recarea'}, {'id': '5', 'latitude': 38.514529, 'longitude': -95.704914, 'bipartite': 'recarea'}, {'id': '6', 'latitude': 39.08333, 'longitude': -96.895, 'bipartite': 'recarea'}, {'id': '7', 'latitude': 39.118462, 'longitude': -95.411396, 'bipartite': 'recarea'}, {'id': '8', 'latitude': 38.65167, 'longitude': -95.55667, 'bipartite': 'recarea'}, {'id': '9', 'latitude': 39.255872, 'longitude': -96.589657, 'bipartite': 'recarea'}, {'id': '10', 'latitude': 38.256722, 'longitude': -94.656428, 'bipartite': 'recarea'}, {'id': '11', 'latitude': 38.679139, 'longitude': -96.505389, 'bipartite': 'recarea'}, {'id': '12', 'latitude': 38.242782, 'longitude': -95.75

Also get recreation area name from recareas database. Look at each rec area coordinates and find coordinates in nodes then add the attribute.

In [46]:
print(nodes)
recareas = json.load(open("./recreation.areas/RecAreas_API_v1.json"))
recdata = recareas.get("RECDATA")
for area in recdata:
    lat1 = area.get("RecAreaLatitude")
    lon1 = area.get("RecAreaLongitude")
    matched = False
    for node in nodes:
        lat2 = float(node.get("latitude"))
        lon2 = float(node.get("longitude"))
        
        if lat1 == lat2 and lon1 == lon2:
            matched = True
            node['recarea'] = area.get("RecAreaName")
            continue
    
    if not matched:
        node['recarea'] = 'None'

print(nodes)        

[{'id': '1', 'latitude': 39.0229714, 'longitude': -94.7145415, 'bipartite': 'city', 'city': 'Shawnee'}, {'id': '2', 'latitude': 38.312105, 'longitude': -95.962768, 'bipartite': 'recarea'}, {'id': '3', 'latitude': 38.92333, 'longitude': -95.33, 'bipartite': 'recarea'}, {'id': '4', 'latitude': 38.654905, 'longitude': -94.900047, 'bipartite': 'recarea'}, {'id': '5', 'latitude': 38.514529, 'longitude': -95.704914, 'bipartite': 'recarea'}, {'id': '6', 'latitude': 39.08333, 'longitude': -96.895, 'bipartite': 'recarea'}, {'id': '7', 'latitude': 39.118462, 'longitude': -95.411396, 'bipartite': 'recarea'}, {'id': '8', 'latitude': 38.65167, 'longitude': -95.55667, 'bipartite': 'recarea'}, {'id': '9', 'latitude': 39.255872, 'longitude': -96.589657, 'bipartite': 'recarea'}, {'id': '10', 'latitude': 38.256722, 'longitude': -94.656428, 'bipartite': 'recarea'}, {'id': '11', 'latitude': 38.679139, 'longitude': -96.505389, 'bipartite': 'recarea'}, {'id': '12', 'latitude': 38.242782, 'longitude': -95.75

In [51]:
import networkx as nx 

G = nx.DiGraph()
# edges = [ {'source':e.get('data').get('source'), 'target':e.get('data').get('target'),'time(s)':e.get('data').get('time'),'distance(km)':e.get('data').get('distance')} for e in edges ]
print(edges)
print(nodes)

for node in nodes:
    id = int(node.get("id"))
    lat = float(node.get("latitude"))
    lon = float(node.get("longitude"))
    bip = node.get("bipartite")
    city = node.get("city")
    recarea = node.get("recarea")
    G.add_node(id, latitude=lat, longitude=lon, bipartite=bip, city = city, recarea = recarea)
        

for edge in edges:
    source = int(edge.get("source"))
    target = int(edge.get("target"))
    time = float(edge.get("time(s)"))
    distance = float(edge.get("distance(km)"))
    G.add_edge(source,target, time = time, distance = distance)

[{'source': 1, 'target': 2, 'time(s)': 5445.753, 'distance(km)': 157.395}, {'source': 1, 'target': 3, 'time(s)': 2520.509, 'distance(km)': 69.909}, {'source': 1, 'target': 4, 'time(s)': 2222.561, 'distance(km)': 51.878}, {'source': 1, 'target': 5, 'time(s)': 4433.356, 'distance(km)': 132.925}, {'source': 1, 'target': 6, 'time(s)': 7157.786, 'distance(km)': 217.877}, {'source': 1, 'target': 7, 'time(s)': 3094.422, 'distance(km)': 83.677}, {'source': 1, 'target': 8, 'time(s)': 4397.53, 'distance(km)': 103.062}, {'source': 1, 'target': 9, 'time(s)': 6741.964, 'distance(km)': 199.929}, {'source': 1, 'target': 10, 'time(s)': 3012.385, 'distance(km)': 90.784}, {'source': 1, 'target': 11, 'time(s)': 6623.246, 'distance(km)': 193.897}, {'source': 1, 'target': 12, 'time(s)': 4737.727, 'distance(km)': 142.558}, {'source': 1, 'target': 13, 'time(s)': 7988.364, 'distance(km)': 219.506}, {'source': 1, 'target': 14, 'time(s)': 7711.795, 'distance(km)': 227.438}, {'source': 1, 'target': 15, 'time(s)'

In [54]:
print(G.nodes(data=True))
data = nx.cytoscape_data(G)
print(data)

with open('./networks/outdoor_recreation_network_USA_augmented.json', 'w', encoding='utf-8') as f:
    json.dump(data, f, ensure_ascii=False, indent=4)



[(1, {'latitude': 39.0229714, 'longitude': -94.7145415, 'bipartite': 'city', 'city': 'Shawnee', 'recarea': None}), (2, {'latitude': 38.312105, 'longitude': -95.962768, 'bipartite': 'recarea', 'city': None, 'recarea': 'Flint Hills National Wildlife Refuge'}), (3, {'latitude': 38.92333, 'longitude': -95.33, 'bipartite': 'recarea', 'city': None, 'recarea': 'Clinton Lake'}), (4, {'latitude': 38.654905, 'longitude': -94.900047, 'bipartite': 'recarea', 'city': None, 'recarea': 'Hillsdale Lake'}), (5, {'latitude': 38.514529, 'longitude': -95.704914, 'bipartite': 'recarea', 'city': None, 'recarea': 'Melvern Lake'}), (6, {'latitude': 39.08333, 'longitude': -96.895, 'bipartite': 'recarea', 'city': None, 'recarea': 'Milford Lake'}), (7, {'latitude': 39.118462, 'longitude': -95.411396, 'bipartite': 'recarea', 'city': None, 'recarea': 'Perry Lake'}), (8, {'latitude': 38.65167, 'longitude': -95.55667, 'bipartite': 'recarea', 'city': None, 'recarea': 'Pomona Lake'}), (9, {'latitude': 39.255872, 'long